## License

Copyright 2020 Google LLC

Licensed under the the Apache License v2.0 with LLVM Exceptions (the "License");
you may not use this file except in compliance with the License.
You may obtain a copy of the License at

https://llvm.org/LICENSE.txt

Unless required by applicable law or agreed to in writing, software
distributed under the License is distributed on an "AS IS" BASIS,
WITHOUT WARRANTIES OR CONDITIONS OF ANY KIND, either express or implied.
See the License for the specific language governing permissions and
limitations under the License.

In [ ]:
import requests
import os
import logging
import argparse
import json
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns

In [ ]:
cache_file = "cache.json"
token = f'Bearer {os.getenv("BUILDKITE_API_TOKEN")}'
builds = []

In [ ]:
if os.path.exists(cache_file):
    with open(cache_file) as f:
        builds = json.load(f)
        print(f'loaded {len(builds)} entries') 

In [ ]:
# load new jobs from Buildkite API
max_pages = 2000
if True:
    existing = set()
    for j in builds:
        existing.add(j['id'])

    # uncomment to reset
#     builds = []
#     existing = set()
    page = 1
    stop = False
    while page <= max_pages:
        print('loading page', page)
        re = requests.get('https://api.buildkite.com/v2/organizations/llvm-project/builds',
                          params={'page': page},
                          headers={'Authorization': token})
        if re.status_code != 200:
            print('response status', re.status_code, re)
            break
        x = re.json()
        if x == []:
            print('empty response')
            break
        for j in x:
            if j['id'] in existing:
#                 print('found existing job', j['id'])
                # load some more pages as some of them might be running before and wasn't added.                
                max_pages = min(page + 5, max_pages)
            else:
                # skip running jobs            
                if (j['state'] == 'running') or (j['state'] == 'scheduled'):
                    print(j['web_url'], 'is', j['state'], ', skipping')
                    continue
                builds.append(j)
        page += 1
    print(len(builds), 'jobs in total')    
    with open(cache_file, 'w') as f:
        json.dump(builds, f)
    print(f'saved {len(builds)} entries')

In [ ]:
d = {
    'id': [],
    'number': [],
    'pipeline': [],
}

jobs = {
    'pipeline': [],
    'name': [],
    'step_key': [],
    'state': [],
    'exit_status': [],
    'agent_id': [],
    
    'agent_name': [],
    'runnable_at': [],
    'started_at': [],
    'wait_duration': [],
    'finished_at': [],
    'run_duration': [],
}

sec = np.timedelta64(1, 's')

for b in builds:
    env = b['env']
#     if 'ph_windows_agents' not in env:
#         continue
#     if 'scripts_branch' not in env:
#         continue
    d['id'].append(b['id'])
    d['number'].append(b['number'])
    d['pipeline'].append(b['pipeline']['slug'])
    for x in b['jobs']:
        if x['state'] in ['waiting_failed', 'canceled', 'skipped', 'broken']:
            continue
        try:
            jobs['pipeline'].append(b['pipeline']['slug'])
            jobs['name'].append(x['name'])
            jobs['step_key'].append(x['step_key'] if 'step_key' in x else '')
            jobs['state'].append(x['state'] )
            jobs['exit_status'].append(x['exit_status'] if 'exit_status' in x else -1)
            jobs['agent_id'].append(x['agent']['id'] if 'agent' in x else '')
            jobs['agent_name'].append(x['agent']['name'] if 'agent' in x else '')
            runnable = np.datetime64(x['runnable_at'].replace('Z', ''))
            started = np.datetime64(x['started_at'].replace('Z', ''))
            finished = np.datetime64(x['finished_at'].replace('Z', ''))
            jobs['runnable_at'].append(runnable)
            jobs['started_at'].append(started)
            jobs['wait_duration'].append((started - runnable) / sec)
            jobs['finished_at'].append(finished)
            jobs['run_duration'].append((finished - started) / sec)
        except Exception as e:
            print(x)
            raise e            
jobs = pd.DataFrame(jobs)

In [ ]:
jobs.pipeline.unique()

In [ ]:
jobs

In [ ]:
# ds = jobs[jobs['pipeline'] == 'llvm-master-build'][jobs['step_key'] == 'windows'][jobs['state']=='passed'][~jobs['agent_name'].str.startswith('buildkite-')][jobs['started_at'] > np.datetime64('2020-01-22')]
ds = jobs[jobs['pipeline'] == 'llvm-master-build'][jobs['step_key'] == 'windows'][jobs['state']=='passed'][~jobs['agent_name'].str.startswith('buildkite-')][jobs['started_at'] > np.datetime64('2020-01-22')]
ds = ds.drop_duplicates()
# remove one slowest run (repo checkout)
# t = ds.loc[ds.groupby(["agent_name"])["run_duration"].idxmax()]
# ds = pd.concat([ds, t]).drop_duplicates(keep=False)

In [ ]:
fig, ax = plt.subplots(figsize=(10,10)) # size of the plot (width, height)

sns.swarmplot(
      ax=ax,
      x='run_duration',
      y='agent_name',
      split=True,
      data=ds)

plt.xlim(0, None)

In [ ]:
t = pd.pivot_table(ds, values=['run_duration'], index=['agent_name'],
                    aggfunc=[np.median, np.mean, np.std, np.count_nonzero])
t = t.reindex(t.sort_values(by=('median', 'run_duration'), ascending=False).index)
t

```
// TODO: try with w64 w/o AV (temporary disabled)
w1 - 16 - non ssd 100 + ssd
w1a - 16 - non ssd 100 + ssd - AV (temp)
w4a - 16 - non ssd 100 + ssd - AV
w16-1 - 16 - non sdd 200 + ssd
w32-1 - 32 - non ssd 100 + ssd
w32-2 - 32 - non ssd 100 + ssd - AV
w32-2d - 32 - non ssd 200 + ssd
w64 - 64 - ssd 200 + ssd 
w64a - 64 - ssd 200 + ssd - AV (temp)
wh63-3 - 64 low ram - non ssd 100 + ssd - AV

buildkite-windows-16n1-exp
gcloud beta compute instances create "${NAME}" \
  --project="${GCP_PROJECT}" \
  --zone="${GCP_ZONE}" \
  --machine-type=n1-standard-16 \
  --local-ssd=device-name=local-ssd-0 \
  --image=windows-server-2019-dc-for-containers-v20200714 \
  --image-project=windows-cloud \
  --boot-disk-size=200GB --boot-disk-type=pd-ssd

buildkite-32-experimental-1
gcloud beta compute instances create "${NAME}" \
  --project="${GCP_PROJECT}" \
  --zone="${GCP_ZONE}" \
  --machine-type=n1-standard-32 \
  --local-ssd=device-name=local-ssd-0 \
  --image=windows-server-2019-dc-for-containers-v20200714 \
  --image-project=windows-cloud \
  --boot-disk-size=200GB --boot-disk-type=pd-ssd

  
buildkite-16c2-exp
gcloud beta compute instances create "${NAME}" \
  --project="${GCP_PROJECT}" \
  --zone="${GCP_ZONE}" \
  --machine-type=c2-standard-16 \
  --local-ssd=device-name=local-ssd-0 \
  --local-ssd=interface=SCSI \
  --image=windows-server-2019-dc-for-containers-v20200714 \
  --image-project=windows-cloud \
  --boot-disk-size=200GB --boot-disk-type=pd-ssd
  
...a: as is D:/ is a workdir (ealy run with full cache build)
...b: C:/ws as a workdir, no cache
...c: c:/ws as workdir, no av
```
